<a href="https://colab.research.google.com/github/HajarahM/Mistral-7B/blob/main/Chat_with_MultiplePDFs_Mistral_7B_Instruct1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
%pip install langchain
%pip install torch
%pip install sentence_transformers
%pip install faiss-cpu
%pip install huggingface-hub
%pip install pypdf
%pip -q install accelerate
%pip install llama-cpp-python
%pip -q install git+https://github.com/huggingface/transformers


In [1]:
from langchain.chains import RetrievalQA
from langchain.embeddings import OllamaEmbeddings
from langchain.llms import Ollama
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.vectorstores import FAISS
from langchain.document_loaders import PyPDFDirectoryLoader
from langchain.document_loaders import DirectoryLoader
from langchain.document_loaders import PyPDFium2Loader
import ocrmypdf
import os

In [2]:
#load pdf files
#os.environ["TOKENIZERS_PARALLELISM"] = "true"
documents = []
processed_directories=0
for dir in os.listdir("data"):
    try: 
        dir_path = './data/'+dir
        loader = PyPDFDirectoryLoader(dir_path)
        documents.extend(loader.load())
        processed_directories+=1
    except:
        print("issue with ", dir)
        pass
print("processed ",processed_directories," directories")

Multiple definitions in dictionary at byte 0xd342d for key /Info
Multiple definitions in dictionary at byte 0xd343a for key /Info
Multiple definitions in dictionary at byte 0xd3447 for key /Info


processed  4  directories


In [3]:
print(documents)

[Document(page_content='STATUTORY INSTRUMENTSSUPPLEMENT No. 14 2nd June, 2016STATUTORY INSTRUMENTS SUPPLEMENTto The Uganda Gazette No. 39, Volume CIX, dated 2nd June, 2016Printed by UPPC, Entebbe, by Order of the Government.STATUTORY INSTRUMENTS2016 No. 34.THE PETROLEUM (REFINING, CONVERSION, TRANSMISSION AND MIDSTREAM STORAGE) (NATIONAL CONTENT) REGULATIONS, 2016.ARRANGEMENT OF REGULATIONSRegulationPARTI—PRELIMINARY1. Title.2. Application.3. Purpose of Regulations.4. Interpretation.PARTII—MONITORINGANDIMPLEMENTATION OFNATIONALCONTENTGeneral Provisions5. National content monitoring. 6. National content during licensing. 7. Submission of national content programme.8. Plan for giving preference for goods and services available inUganda.Procurement Requirements9. Submission of procurement forecasts to Authority.10. Priority for Ugandan goods and services during procurement.11. Contracts goods and services to be provided by Ugandan Companies,registered entities and Ugandan citizens.289', m

In [8]:
#Step 05: Split the Extracted Data into Text Chunks
text_splitter = RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=50, separators=['\n\n', '\n', '.'])

text_chunks = text_splitter.split_documents(documents)


In [9]:
len(text_chunks)

14586

In [10]:
#get the third chunk
text_chunks[30]

Document(page_content='.(4) Where a Ugandan company, registered entity or Ugandancitizen is unable to provide the required quality of goods and servicesdue to lack of technical capacity or financial competence, the licenseemay, with the approval of the Authority, procure the goods and servicesfrom any other company within a period specified by the Authority.298', metadata={'source': 'data/Petroleum/Midstream National Content Regulations 2016.pdf', 'page': 9})

In [12]:
#Step 06:Downlaod the Embeddings
embeddings = OllamaEmbeddings(model="mistral")

In [13]:
from langchain.embeddings.sentence_transformer import SentenceTransformerEmbeddings
embedding_model = SentenceTransformerEmbeddings(model_name='all-mpnet-base-v2')

In [16]:
from langchain.vectorstores import Chroma
vector_store = Chroma.from_documents(text_chunks, embedding=embedding_model, persist_directory="./vector_db")
vector_store.persist()
print('saved embeddings to vector_store')

saved embeddings to vector_store


In [15]:
#Step 08: Create Embeddings for each of the Text Chunk
import os
vector_store = FAISS.from_documents(text_chunks, embedding=embedding_model)
print('saving embeddings to vector_store')
folder_path="FAISS_vector_store"
if os.path.exists(folder_path):
    faiss_index=FAISS.load_local(folder_path, embeddings)
    faiss_index.merge_from(vector_store)
    faiss_index.save_local(folder_path)
else:
    vector_store.save_local(folder_path)

saving embeddings to vector_store


In [23]:
#Import Model
from langchain.llms import Ollama
from langchain.callbacks.manager import CallbackManager
from langchain.callbacks.streaming_stdout import StreamingStdOutCallbackHandler
llm = Ollama(
    base_url="http://localhost:11434",
    model = "mistral",
    verbose=True,
    callback_manager = CallbackManager([StreamingStdOutCallbackHandler()])
    )
#vector_store_path = "./FAISS_vector_store"
#vector_store = Chroma(vector_store_path, embedding_model)
qa = RetrievalQA.from_chain_type(llm=llm, chain_type="stuff", retriever=vector_store.as_retriever(search_kwargs={"k": 4}))
query = "Summarize the Mining Act commencement instrument of 2004"
qa.run(query)



The Mining Act Commencement Instrument of 2004 was issued under section 1(2) of the Mining Act, 2003. It provided for the future payment of remedial work to the licence area covered by a mining right and managed jointly by the licensee and the Minister responsible for mining operations. The instrument also defined "mining exploration expenditure" and "mining information". Specifically, "mining exploration expenditure" refers to expenses incurred in search for minerals under a mining exploration right, while "mining information" refers to any other information relating to mining exploration apart from that specified in paragraph (a)(ii) of the definition.

The instrument further provides for social infrastructure expenditure incurred in accordance with a mining lease. It also outlines the procedure for confirming minutes related to petroleum operations and signing them by the Chairperson, in the presence of members present at the latter meeting. Lastly, it relates to the Petroleum (Exp

'\nThe Mining Act Commencement Instrument of 2004 was issued under section 1(2) of the Mining Act, 2003. It provided for the future payment of remedial work to the licence area covered by a mining right and managed jointly by the licensee and the Minister responsible for mining operations. The instrument also defined "mining exploration expenditure" and "mining information". Specifically, "mining exploration expenditure" refers to expenses incurred in search for minerals under a mining exploration right, while "mining information" refers to any other information relating to mining exploration apart from that specified in paragraph (a)(ii) of the definition.\n\nThe instrument further provides for social infrastructure expenditure incurred in accordance with a mining lease. It also outlines the procedure for confirming minutes related to petroleum operations and signing them by the Chairperson, in the presence of members present at the latter meeting. Lastly, it relates to the Petroleum 

In [24]:
from langchain.llms import Ollama
from langchain.callbacks.manager import CallbackManager
from langchain.callbacks.streaming_stdout import StreamingStdOutCallbackHandler
llm = Ollama(
    base_url="http://localhost:11434",
    model = "zephyr",
    verbose=True,
    callback_manager = CallbackManager([StreamingStdOutCallbackHandler()])
    )

In [25]:
from langchain import hub
QA_CHAIN_PROMPT = hub.pull("rlm/rag-prompt")

In [26]:
def retrieval_qa_chain(llm, vector_store):
    qa_chain = RetrievalQA.from_chain_type(
        llm,
        retriever = vector_store.as_retriever(),
        chain_type = "mmr",
        chain_type_kwargs={"prompt": QA_CHAIN_PROMPT},
        return_source_documents=True
    )
    return qa_chain

In [27]:
def qa_bot():
    db_path = "vector_db/"
    vectorstore = Chroma(db_path,embedding_model)
    qa = retrieval_qa_chain(llm, vectorstore)
    return qa

query = "Summarize the Mining Act commencement instrument of 2004"
qa.run(query)


The Mining Act Commencement Instrument of 2004 was published under Statutory Instruments Supplement No. 42, dated 10th December, 2004. It was issued in exercise of the powers conferred upon the Minister by section 1(2) of the Mining Act, 2003. The instrument provides for the future payment of remedial work to the licence area covered by the mining right and that is managed jointly by the licensee and the Minister responsible for mining operations.

The instrument defines "mining exploration expenditure" under section (a)(i) to include any costs incurred in searching for minerals under a mining exploration right. Section (a)(ii) provides that mining information, other than information referred to in paragraph (a)(ii) of the definition of "mining exploration expenditure", shall also be considered mining exploration expenditure.

The instrument defines "social infrastructure expenditure" as any costs incurred by a licensee in accordance with a mining lease for social infrastructure purpo

'\nThe Mining Act Commencement Instrument of 2004 was published under Statutory Instruments Supplement No. 42, dated 10th December, 2004. It was issued in exercise of the powers conferred upon the Minister by section 1(2) of the Mining Act, 2003. The instrument provides for the future payment of remedial work to the licence area covered by the mining right and that is managed jointly by the licensee and the Minister responsible for mining operations.\n\nThe instrument defines "mining exploration expenditure" under section (a)(i) to include any costs incurred in searching for minerals under a mining exploration right. Section (a)(ii) provides that mining information, other than information referred to in paragraph (a)(ii) of the definition of "mining exploration expenditure", shall also be considered mining exploration expenditure.\n\nThe instrument defines "social infrastructure expenditure" as any costs incurred by a licensee in accordance with a mining lease for social infrastructure

In [ ]:
import sys

while True:
  user_input = input(f"Input Prompt: ")
  if user_input == 'exit':
    print('Exiting')
    sys.exit()
  if user_input == '':
    continue
  result = qa({'query': user_input})
  print(f"Answer: {result['result']}")